# Hamiltonian Learning via Quantum Zeno Effect: A Tutorial

This tutorial demonstrates how to run the algorithm described in  **Hamiltonian learning via quantum Zeno effect**.

In [1]:
import os
import subprocess
import json
import numpy as np
from tqdm import tqdm
import time

## Step 2: Data Extraction Utilities

The function uses regular expressions to parse structured text files containing our Hamiltonian learning results.

In [2]:
import re

def extract_field(file_path, field_name):
    with open(file_path, 'r') as file:
        content = file.read()
    
    # Special handling for Choi Matrices field
    if field_name == "Choi Matrices":
        choi_dict = {}
        # Find the Choi Matrices block
        match = re.search(rf'{field_name}:\s*(.*?)\n[A-Za-z]|\Z', content, re.DOTALL)
        if match:
            block = match.group(1)
            if block is None:
                match = re.search(rf'{re.escape("Choi Matrices")}:\s*([\s\S]*)$', content, re.DOTALL| re.MULTILINE)
                block = match.group(1)
            # Find all matrix labels and their arrays
            for label, arr_str in re.findall(r'(\w+):\n(\[\[.*?\]\])', block, re.DOTALL):
                # arr_str is a string representation of a numpy array, convert it to a numpy array, like [[1 2\n\ 3 4]], handle 
                choi_dict[label] = np.array(eval(re.sub(r"\s{2,}", " ", arr_str).replace('[ ', '[').replace(' ]', ']').replace(' ', ',')))
        return choi_dict

    # Try to match a list (e.g., Differences, Coefficients)
    match_list = re.search(f'{field_name}:\n\[(.*?)\]', content, re.DOTALL)
    if match_list:
        values_str = match_list.group(1)
        values = [float(x.replace(',', '')) for x in values_str.split()]
        return values
    return None

## Step 3: Parameter Setup

Now we'll define our experimental parameters for the batch Hamiltonian learning study. We're investigating how reconstruction accuracy depends on:

**Parameters:**
- **N**: Chain length (number of qubits in the spin chain)
- **N_QPT**: Local system size for tomography (typically 2 for nearest-neighbor interactions)
- **T**: Total evolution time of the Hamiltonian
- **n_steps**: Number of Zeno measurement "kicks" during evolution
- **N_shots**: Number of measurement shots (statistical samples)
- **shots_vec**: Range of measurement budgets to test
- **N_vec**: Different chain lengths to study scaling behavior

In [3]:
# Define the sets of parameters you want to use
parameter_sets = []
shots_vec = [1e2, 1e3, 1e4, 1e5, 1e6, 1e7]
N_vec = [3, 6, 9, 16, 32, 64, 128]
n_averages = 10
for shots in shots_vec:
    for N in N_vec:
        for i in range(n_averages):
            params = {
                "N": N, "N_QPT": 2, "T": 1e-2, "n_steps": 10, "N_shots": int(shots), "plot": False, "save": True, "seed": i
            }
            parameter_sets.append(params)

## Step 4: Batch Hamiltonian Learning Execution

This is where we run our Hamiltonian learning experiments using the quantum Zeno effect! The code below:

1. **Creates configuration files** for each parameter set
2. **Runs the main Hamiltonian learning script** (`hl_w_zeno_TN.py`) with tensor network methods
3. **Organizes results** into properly named files in the data folder
4. **Cleans up** temporary configuration files

**What's happening in each run:**
- **Initialize unknown Hamiltonian**: Create a random local Hamiltonian with nearest-neighbor interactions
- **Implement Zeno protocol**: Apply frequent measurements to auxiliary qubits to freeze their evolution
- **Local tomography**: Perform quantum process tomography on small subsystems (2-qubit patches)
- **Coefficient extraction**: Reconstruct the Hamiltonian parameters from measurement data
- **Performance evaluation**: Compare reconstructed vs. true coefficients

⚠️ **Note:** This may take a while depending on your parameter ranges! Each run involves multiple Zeno measurement cycles and local tomography procedures.

In [ ]:
# Path to the main script
script_path = "./hl_w_zeno_TN.py"
average_counter = 0
# Loop over the parameter sets and run the main script with each set
for params in tqdm(parameter_sets):
    i = average_counter
    config_path = f"./config_{i}.json"
    
    # Save the parameters to a config file
    with open(config_path, 'w') as f:
        json.dump(params, f)
    # Run the main script with the config file
    subprocess.run(["python", script_path, "--config", config_path])
    
    # Rename output file as coeff_res_dt_{dt}_{i}.txt and move it to the ./data folder, current name is "results.txt"
    # overwriting the destination file if it already exists
    os.replace("./results.txt", f"./data/paper/N_{params['N']}_T_{params['T']}_n_shots_{params['N_shots']}_{i-(i//n_averages)*n_averages}.txt")
    if average_counter == n_averages - 1:
        average_counter = 0
    else:
        average_counter += 1
    # remove the config file after execution
    os.remove(config_path)

## Step 5: Hamiltonian Reconstruction Analysis

Now we'll load and analyze our Hamiltonian learning results.

In [12]:
# Load the data
data = {}
vars = {}
for N in N_vec:
    data[N] = {}
    vars[N] = {}
    for shots in shots_vec:
        data[N][shots] = 0
        vars[N][shots] = []

for i in range(len(parameter_sets)):
    file_name = f"./data/paper/N_{parameter_sets[i]['N']}_T_{parameter_sets[i]['T']}_n_shots_{parameter_sets[i]['N_shots']}_{i-(i//n_averages)*n_averages}.txt"
    # put in data the square root of the sum of the squares of the differences
    try:
        data[parameter_sets[i]['N']][parameter_sets[i]['N_shots']] += np.sqrt(np.sum(np.square(extract_field(file_name, 'Differences'))))/n_averages
        vars[parameter_sets[i]['N']][parameter_sets[i]['N_shots']].append(np.sqrt(np.sum(np.square(extract_field(file_name, 'Differences')))))
    except:
        reconstructed = extract_field(file_name, 'Reconstructed Coefficients')
        real = extract_field(file_name, 'Real Coefficients')
        differences = np.array(reconstructed) - np.array(real)
        data[parameter_sets[i]['N']][parameter_sets[i]['N_shots']] += np.sqrt(np.sum(np.square(differences)))/n_averages
        vars[parameter_sets[i]['N']][parameter_sets[i]['N_shots']].append(np.sqrt(np.sum(np.square(differences))))

In [13]:
N_factor = {3: 2, 6: 3, 9: 3, 16: 3, 32: 3, 64: 3, 128: 3}

## Step 7: Hamiltonian Learning Performance Visualization

Finally, let's plot the results reproducing a figure of the paper.

**What this plot shows:**
- **X-axis**: Total number of measurement copies (shots × 16² × scaling factor)
- **Y-axis**: Hamiltonian reconstruction error ||Δc||₂ (logarithmic scale)
- **Different curves**: Various spin chain lengths (N = 3, 6, 9, ...)
- **Error bars**: Statistical uncertainty from multiple independent learning runs

In [14]:
from matplotlib.colors import to_rgb
import numpy as np

import matplotlib.pyplot as plt

# Use three well-separated colors: lilla, yellow, green
palette = [
   # "#9884b9",   # lilla (original)
   # "#A9CBB7",   # yellow (distinct, from colorblind-friendly palettes)
   # "#F79D5C",   # green (distinct, from colorblind-friendly palettes)
    "#C9BEDA",
    "#b3a3cc",
    "#9884B9",
    "#7a6a91",
    "#604A82",
    "#463069",
    "#2b254a"
]

fig, ax = plt.subplots(1, 1, figsize=(4.5, 3.8), dpi=2500)

for idx, N in enumerate(N_vec):
    color = palette[idx % len(palette)]
    x = np.array(list(data[N].keys())[1:])
    y = np.array(list(data[N].values())[1:])
    yerr = [np.sqrt(np.var(vars[N][k])) for k in x]
    ax.plot(x*16*16*N_factor[N], y, 'o-', label=f'N={N}', color=color)
    ax.fill_between(x*16*16*N_factor[N], y - yerr, y + yerr, alpha=0.2, color=color)

ax.set_yscale('log')
ax.set_xscale('log')
ax.set_xlabel('number of copies', fontsize=12)
ax.set_ylabel('$||\Delta c||_2$', fontsize=12)
ax.grid(True, which='major', linestyle='--', linewidth=0.5)
#ax.grid(True, which='minor', linestyle=':', linewidth=0.2)
plt.legend()

for label in (ax.get_xticklabels() + ax.get_yticklabels()):
    label.set_fontsize(10)

plt.title(f'T = {parameter_sets[0]["T"]}', fontsize=13)
plt.tight_layout()
plt.show()
